In [12]:
import zfit
import math
from zfit import z
import numpy as np
import tensorflow as tf
from scipy.optimize import minimize

zfit.settings.options['numerical_grad'] = True
class HistPDF(zfit.pdf.BasePDF):

    def __init__(self, hist_args, hist_bins, obs, name='HistPDF'):
        self.rv_hist = scipy.stats.rv_histogram([hist_args, hist_bins])
        super().__init__(obs=obs, name=name)

    def _unnormalized_pdf(self, x):
        x = z.unstack_x(x)
        probs =  z.py_function(func=self.rv_hist.pdf, inp=[x], Tout=tf.float64)
        probs.set_shape(x.shape)
        return probs

In [5]:
# mu2 = zfit.Parameter("mu2", 5., step_size=0)
# sigma2 = zfit.Parameter("sigma2", 1., step_size=0)
# lambd2 = zfit.Parameter("lambda2", -0.2, step_size=0)
# frac2 = zfit.Parameter("fraction2", 0.5, 0, 1)
# frac1 = zfit.Parameter("fraction1", 0.5, step_size=0)
# create space
obs1 = zfit.Space("x", limits=(0, 10))
obs2 = zfit.Space("x", limits=(0, 10))

# parameters
mu1 = zfit.Parameter("mu1", 5., 1, 10, step_size=0)
sigma1 = zfit.Parameter("sigma1", 1., 0.1, 10, step_size=0)
lambd1 = zfit.Parameter("lambda1", -0.2, -1, -0.01, step_size=0)
frac1 = zfit.Parameter("fraction1", 0.5, 0, 1)

mu2 = zfit.Parameter("mu2", 5., step_size=0)
sigma2 = zfit.Parameter("sigma2", 1., step_size=0)
lambd2 = zfit.Parameter("lambda2", -0.2, step_size=0)
frac2 = zfit.Parameter("fraction2", 0.5, step_size=0)




gauss1 = zfit.pdf.Gauss(mu=mu1, sigma=sigma1, obs=obs1)
exponential1 = zfit.pdf.Exponential(lambd1, obs=obs1)
model1 = zfit.pdf.SumPDF([gauss1, exponential1], fracs=frac1)


gauss2 = zfit.pdf.Gauss(mu=mu2, sigma=sigma2, obs=obs2)
exponential2 = zfit.pdf.Exponential(lambd2, obs=obs2)
model2 = zfit.pdf.SumPDF([gauss2, exponential2], fracs=frac2)

In [6]:
n_sample = 10000

exp_data = exponential2.sample(n=n_sample * (1 - frac1)).numpy()

gauss_data = gauss2.sample(n=n_sample * frac1).numpy()

data = model1.create_sampler(n_sample, limits=obs1)
data.resample()

In [7]:
data_np = data[:, 0].numpy()
exp_data_np = exp_data[:, 0]
gauss_data_np = gauss_data[:, 0]

In [8]:
data_hist = np.histogram(data_np, bins=100)
exp_data_hist = np.histogram(exp_data_np, bins=100)
gauss_data_hist = np.histogram(gauss_data_np, bins=100)
sim_hists = []
sim_hists.append(exp_data_hist)
sim_hists.append(gauss_data_hist)

In [55]:
class FractionFitter(object):

    def __init__(self, data_hist, sim_hists, P):
        self.data_hist = data_hist
        self.P = P
        self.sim_hists = [hist for hist in sim_hists]
        self.d = self.data_hist[0] # where d[i] amount of sources in bin from data
        self.N_D = np.sum(self.data_hist[0])#all observable data amount
        self.N = [np.sum(h[0]) for h in sim_hists]# amount of simulation data from sources e.g. N[0] from source 0 .. N[j] from source j
        self.sources_num = len(P)
        self.bins_num = len(data_hist[0])
        
    def norma(self, v):
        return math.sqrt(sum(vi ** 2 for vi in v))
            
    def f(self, t, a, p, i):
        if self.d[i] == 0:
            return 1
        else:
            return np.abs(np.sum((p[:] * a[:, i] / (1 + p[:] * t))) * (1 - t) - self.d[i])
    
    def sqF(self, p, A):
        res = 0
        for j in range(self.sources_num):
            tmp_res = 0
            for i in range(self.bins_num):
                tmp_res += (self.d[i] * A[j][i])/np.sum(p[:] * A[:, i])
            res += tmp_res**2
            
        return res
                
    def div_sqF(self, p, k, A):
        res = 0
        for j in range(self.sources_num):
            sum1 = 0
            sum2 = 0
            for i in range(self.bins_num):
                sum1 -= (self.d[i] * A[j][i] * p[k] * A[k][i])/(np.sum(p[:] * A[:, i]))**2
                sum2 += (self.d[i] * A[j][i])/np.sum(p[:] * A[:, i])
            res += sum1*sum2
        return res
            

    def fit(self, eps):
        # let assume initial set of p_j:
        p = []
        p_new = []
        for i in range(self.sources_num):
            p.append(self.N_D*self.P[i]/self.N[i])
        p_new = p.copy()

        a = np.array([[0] * self.bins_num for i in range(self.sources_num)])#a[j][i] amount of observations in i bin from j source
        for j in range(self.sources_num):
            for i in range(self.bins_num):
                a[j][i] = self.sim_hists[j][0][i]
        while(True): 
#             t0 = [] # initial values for t
#             for i in range(self.bins_num):
#                 t0.append(1 - self.d[i]/np.sum(p[:]*a[:, i]))
            t = []# t[i] = 1 - d[i]/f[i]
            # t calculating ...
            for i in range(self.bins_num):
                t.append(minimize(self.f, 0, args=(a, p, i), method='nelder-mead', 
                                  options={'xtol': 1e-3, 'disp': True}).x[0])
                
            A = np.array([[0.0] * self.bins_num for i in range(self.sources_num)])#A[j][i] fitted amount of observations in i bin from j source
            for j in range(self.sources_num):
                for i in range(self.bins_num):
                    A[j][i] = a[j][i]/(1 + p[j]*t[i])
                    if(A[j][i] == 0.0):
                        A[j][i] = 0.1
                    
            
            for i in range(len(p)):
                p_new[i] = p[i] - self.sqF(p, A)/self.div_sqF(p, i, A)
            if np.abs(self.norma(p_new) - self.norma(p)) < eps:
                return p_new
            
            print(self.sqF(p, A)/self.div_sqF(p, i, A))
            
            p = p_new.copy()
        
        

        
        
        


In [56]:
fitter = FractionFitter(data_hist=data_hist, sim_hists=sim_hists, P=[0.6, 0.4])

In [57]:
p = []
p = fitter.fit(1e-1)

Optimization terminated successfully.
         Current function value: 0.000125
         Iterations: 24
         Function evaluations: 48
Optimization terminated successfully.
         Current function value: 0.000103
         Iterations: 24
         Function evaluations: 48
Optimization terminated successfully.
         Current function value: 0.000100
         Iterations: 21
         Function evaluations: 42
Optimization terminated successfully.
         Current function value: 0.000070
         Iterations: 25
         Function evaluations: 50
Optimization terminated successfully.
         Current function value: 0.000053
         Iterations: 23
         Function evaluations: 46
Optimization terminated successfully.
         Current function value: 0.000060
         Iterations: 26
         Function evaluations: 52
Optimization terminated successfully.
         Current function value: 0.000108
         Iterations: 22
         Function evaluations: 44
Optimization terminated successful

Optimization terminated successfully.
         Current function value: 0.000092
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000104
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000219
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000242
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000089
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000087
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000195
         Iterations: 27
         Function evaluations: 54
Optimization terminated successful

Optimization terminated successfully.
         Current function value: 0.000073
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000068
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000054
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000064
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000117
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000074
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.004136
         Iterations: 22
         Function evaluations: 44
Optimization terminated successful

Optimization terminated successfully.
         Current function value: 0.000418
         Iterations: 25
         Function evaluations: 50
Optimization terminated successfully.
         Current function value: 0.000121
         Iterations: 26
         Function evaluations: 52
Optimization terminated successfully.
         Current function value: 0.000536
         Iterations: 23
         Function evaluations: 46
Optimization terminated successfully.
         Current function value: 0.000059
         Iterations: 26
         Function evaluations: 52
Optimization terminated successfully.
         Current function value: 0.000235
         Iterations: 25
         Function evaluations: 50
-1.8677105653022748
Optimization terminated successfully.
         Current function value: 0.000779
         Iterations: 26
         Function evaluations: 52
Optimization terminated successfully.
         Current function value: 0.000136
         Iterations: 29
         Function evaluations: 58
Optimization t

Optimization terminated successfully.
         Current function value: 0.000060
         Iterations: 30
         Function evaluations: 60
Optimization terminated successfully.
         Current function value: 0.000099
         Iterations: 29
         Function evaluations: 58
Optimization terminated successfully.
         Current function value: 0.000090
         Iterations: 29
         Function evaluations: 58
Optimization terminated successfully.
         Current function value: 0.000061
         Iterations: 30
         Function evaluations: 60
Optimization terminated successfully.
         Current function value: 0.000059
         Iterations: 30
         Function evaluations: 60
Optimization terminated successfully.
         Current function value: 0.000333
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000058
         Iterations: 30
         Function evaluations: 60
Optimization terminated successful

...

-1.6745011278623512
Optimization terminated successfully.
         Current function value: 0.000198
         Iterations: 29
         Function evaluations: 58
Optimization terminated successfully.
         Current function value: 0.000161
         Iterations: 29
         Function evaluations: 58
Optimization terminated successfully.
         Current function value: 0.000161
         Iterations: 29
         Function evaluations: 58
Optimization terminated successfully.
         Current function value: 0.000429
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000751
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000701
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000102
         Iterations: 30
         Function evaluations: 60
Optimization t

Optimization terminated successfully.
         Current function value: 0.000106
         Iterations: 30
         Function evaluations: 60
Optimization terminated successfully.
         Current function value: 0.000227
         Iterations: 29
         Function evaluations: 58
Optimization terminated successfully.
         Current function value: 0.000105
         Iterations: 30
         Function evaluations: 60
Optimization terminated successfully.
         Current function value: 0.000070
         Iterations: 30
         Function evaluations: 60
Optimization terminated successfully.
         Current function value: 0.000316
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000356
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000320
         Iterations: 28
         Function evaluations: 56
Optimization terminated successful

Optimization terminated successfully.
         Current function value: 0.000070
         Iterations: 30
         Function evaluations: 60
Optimization terminated successfully.
         Current function value: 0.000099
         Iterations: 29
         Function evaluations: 58
Optimization terminated successfully.
         Current function value: 0.000492
         Iterations: 26
         Function evaluations: 52
Optimization terminated successfully.
         Current function value: 0.000448
         Iterations: 26
         Function evaluations: 52
Optimization terminated successfully.
         Current function value: 0.000096
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000158
         Iterations: 27
         Function evaluations: 54
Optimization terminated successfully.
         Current function value: 0.000077
         Iterations: 28
         Function evaluations: 56
Optimization terminated successful

Optimization terminated successfully.
         Current function value: 0.000100
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000388
         Iterations: 26
         Function evaluations: 52
Optimization terminated successfully.
         Current function value: 0.000070
         Iterations: 29
         Function evaluations: 58
Optimization terminated successfully.
         Current function value: 0.000132
         Iterations: 26
         Function evaluations: 52
Optimization terminated successfully.
         Current function value: 0.000068
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000054
         Iterations: 28
         Function evaluations: 56
Optimization terminated successfully.
         Current function value: 0.000946
         Iterations: 24
         Function evaluations: 48
Optimization terminated successful

KeyboardInterrupt: 

In [371]:
a = np.array([[128, 94, 119, 100, 103], [1, 0, 0, 1, 1]])
p = [1.2, 0.8]

In [372]:
def f(t, a, p, i):
    return np.abs(np.sum((p[:] * a[:, i] / (1 + p[:] * t))) * (1 - t) - 131)

In [373]:
t = []
for i in range(5):
    t.append(minimize(f, 0, args=(a, p, i) ,method='nelder-mead', 
                      options={'xtol': 1e-3, 'disp': True}).x[0])


Optimization terminated successfully.
         Current function value: 0.000127
         Iterations: 23
         Function evaluations: 46
Optimization terminated successfully.
         Current function value: 0.000053
         Iterations: 24
         Function evaluations: 48
Optimization terminated successfully.
         Current function value: 0.000093
         Iterations: 21
         Function evaluations: 42
Optimization terminated successfully.
         Current function value: 0.000134
         Iterations: 21
         Function evaluations: 42
Optimization terminated successfully.
         Current function value: 0.000136
         Iterations: 20
         Function evaluations: 40


In [396]:
p

[]

In [390]:
P = []
for j in range(len(p)):
    P.append(p[j] * fitter.N[j]/fitter.N_D)

In [391]:
P

[0.8458708339841029, 0.6604267377798096]

In [430]:
p = [100.8729970684941, 73.80758908842088]
A = np.array([[2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2 ,2, 2, 1 ,1 ,1 ,1,1,1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
  0, 1, 1, 0, 0, 0, 0, 0 ,0, 0, 0 ,0 ,0, 0, 0, 0, 0, 0, 0, 0, 0, 0 ,0 ,0 ,0 ,0, 0, 0, 0, 0, 0, 0, 0 ,0 ,0 ,0,
  0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1 ,1 ,1 ,1 ,1 ,1 ,1 ,1 ,1 ,1 ,1 ,1 ,1, 1, 1, 1, 1],
 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 2, 1,
  2, 2, 2, 2, 2, 2, 3, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 2, 2, 2, 2, 2, 2, 2, 1, 1, 2, 1 ,1,
  1, 1, 1, 1, 1, 1, 1 ,0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]])

In [441]:
fitter.sqF(p, A)

0
0 номер =  0
1.298662712589468 номер =  1
2.250354471433658 номер =  2
3.330921155954666 номер =  3
4.431314752118261 номер =  4
5.501967980817976 номер =  5
6.493313562947341 номер =  6
7.6730148056812855 номер =  7
8.674273843631944 номер =  8
9.47726376515673 номер =  9
10.438868979822214 номер =  10
11.53926257598581 номер =  11
12.371992864974477 номер =  12
13.22455006560573 номер =  13
14.017626531309222 номер =  14
14.88009718776177 номер =  15
15.80204857914208 номер =  16
16.714086514701094 номер =  17
17.665778273545286 номер =  18
18.508422018355247 номер =  19
19.33123885152262 номер =  20
19.935959656621534 номер =  21
20.679468843218558 номер =  22
21.42297802981558 номер =  23
22.107006481484845 номер =  24
22.810861844796694 номер =  25
23.623765222142772 номер =  26
24.43666859948885 номер =  27
25.388360358333042 номер =  28
25.84061439375879 номер =  29
26.310042633061467 номер =  30
26.79664507624107 номер =  31
27.317595927174526 номер =  32
27.815647839605415 н

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:36: RuntimeWarning: invalid value encountered in true_divide


nan